In [1]:
%env CUDA_VISIBLE_DEVICES=1
!pip install accelerate peft bitsandbytes transformers trl

env: CUDA_VISIBLE_DEVICES=1


In [2]:
import csv
import json
import time

import torch
from datasets import load_dataset
from peft import LoraConfig
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    TrainingArguments,
    pipeline,
    logging,
)
from trl import SFTTrainer

/opt/conda/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
# Model from Hugging Face hub
base_model = "llmware/dragon-mistral-7b-v0" #"llmware/bling-phi-3-gguf"

# New instruction dataset
hugging_dataset = "Akhil7766/mistral_2k"

# Fine-tuned model
new_model = "Akhil7766/dragon-mistral-7b-v0-Ryobi_29_May"


In [4]:
from transformers import AutoModel

access_token = "token_from_hugging_face"
model = AutoModel.from_pretrained(base_model, token=access_token)

dataset = load_dataset(hugging_dataset, split="train")

compute_dtype = getattr(torch, "float16")

/opt/conda/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [5]:
quant_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=compute_dtype,
    bnb_4bit_use_double_quant=False,
)

In [6]:
model = AutoModelForCausalLM.from_pretrained(
    base_model,
    quantization_config=quant_config,
    device_map={"": 0}
)
model.config.use_cache = False
model.config.pretraining_tp = 1


In [7]:
tokenizer = AutoTokenizer.from_pretrained(base_model, token=access_token)
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"


In [8]:
peft_params = LoraConfig(
    lora_alpha=16,
    lora_dropout=0.1,
    r=64,
    bias="none",
    task_type="CAUSAL_LM",
)


In [9]:
import os
os.environ['NCCL_P2P_DISABLE'] = '1'
os.environ['NCCL_IB_DISABLE'] = '1'

In [10]:
training_params = TrainingArguments(
    output_dir="./dragon-mistral-7b-v0-Ryobi",
    num_train_epochs=1,
    per_device_train_batch_size=4,
    gradient_accumulation_steps=4,
    optim="paged_adamw_32bit",
    save_steps=25,
    logging_steps=25,
    learning_rate=2e-4,
    weight_decay=0.001,
    fp16=True,
    gradient_checkpointing=True,
    max_grad_norm=0.3,
    max_steps=-1,
    warmup_ratio=0.03,
    group_by_length=True,
    lr_scheduler_type="constant",
    report_to="tensorboard"
)

In [11]:
trainer = SFTTrainer(
    model=model,
    train_dataset=dataset,
    peft_config=peft_params,
    dataset_text_field="text",
    max_seq_length=None,
    tokenizer=tokenizer,
    args=training_params,
    packing=False,
)

/opt/conda/lib/python3.11/site-packages/trl/trainer/sft_trainer.py:246: UserWarning: You didn't pass a `max_seq_length` argument to the SFTTrainer, this will default to 1024
  warnings.warn(


In [12]:
run_time = str(time.time())

In [13]:
system_prompt = """The user wants to find intent for questions related to Ryobi products. The goal is to create JSON from the user input to get the intent of the question. 
    For random gibberish text, send response with empty values (either "" or [] based on examples) 
    """

In [14]:
def testModel(prefix):
    json_file_path = './questionare.json'
    with open(json_file_path, 'r') as json_file:
        questions_data = json.load(json_file)

    responses = [["question","answer"]]
    # Iterate over the questions
    for question in questions_data:
        question = question + "(return only 1 response and response should be in json format)"
        # pipe = pipeline(task="text-generation", model=model, tokenizer=tokenizer, max_length=1200,return_full_text=False,truncation=False)
        # result = pipe(f"<human>: {system_prompt}\n{question}\n<bot>:")
        # print(question,result[0]['generated_text'])
        # responses.append([question,result[0]['generated_text']])
        # {system_prompt}\n
        inputs = tokenizer(f"<human>: {question}\n<bot>:", return_tensors="pt")
        start_of_output = len(inputs.input_ids[0])

        #   temperature: set at 0.3 for consistency of output
        #   max_new_tokens:  set at 100 - may prematurely stop a few of the summaries

        outputs = model.generate(
            inputs.input_ids.to('cuda'),
            eos_token_id=tokenizer.eos_token_id,
            pad_token_id=tokenizer.eos_token_id,
            do_sample=True,
            temperature=0.3,
            max_new_tokens=100,
            )

        output_only = tokenizer.decode(outputs[0][start_of_output:],skip_special_tokens=True)

        # quick/optional post-processing clean-up of potential fine-tuning artifacts

        eot = output_only.find("<|endoftext|>")
        if eot > -1:
            output_only = output_only[:eot]

        bot = output_only.find("<bot>:")
        if bot > -1:
            output_only = output_only[bot+len("<bot>:"):]

        # end - post-processing
        # output_only = output_only[output_only.find('{'):output_only.find('}')+1]

        print("\n")
        print(question, "llm_response - ", output_only)
        responses.append([question,output_only])
    response_path = "./dragon_mistral_500_"+prefix+"_training_" + run_time + ".csv"
    print("saving responses to " + response_path)
    with open(response_path, "w", newline="") as csvfile:
        csv_writer = csv.writer(csvfile)
        csv_writer.writerows(responses)
    print("saved responses to " + response_path)


In [15]:
logging.set_verbosity(logging.CRITICAL)

In [16]:
#testModel("before")

In [17]:
trainer.train()

/opt/conda/lib/python3.11/site-packages/torch/utils/checkpoint.py:464: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


/opt/conda/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/opt/conda/lib/python3.11/site-packages/torch/utils/checkpoint.py:464: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
/opt/conda/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_downlo

TrainOutput(global_step=121, training_loss=1.5359170771827382, metrics={'train_runtime': 160.8481, 'train_samples_per_second': 12.055, 'train_steps_per_second': 0.752, 'total_flos': 3256606022369280.0, 'train_loss': 1.5359170771827382, 'epoch': 0.9979381443298969})

In [18]:
trainer.model.save_pretrained(new_model)
trainer.tokenizer.save_pretrained(new_model)
trainer.model.config.to_json_file("llmware/dragon-mistral-7b-v0-Ryobi/config.json")

/opt/conda/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [19]:
logging.set_verbosity(logging.CRITICAL)
testModel("after")

/opt/conda/lib/python3.11/site-packages/torch/utils/checkpoint.py:91: UserWarning: None of the inputs have requires_grad=True. Gradients will be None
  warnings.warn(




What are the different types of parts and accessories available for the Ryobi Lawn Mower Petrol RM480E?(return only 1 response and response should be in json format) llm_response -  {"intent": "product_enquiry"}


Hello, I would like to inquire about the product categories available(return only 1 response and response should be in json format) llm_response -  {"intent": "product_enquiry"}


Can you explain the differences in part numbers for the products in the Lawn Mower category compared to those in the Nailers & Staplers category?(return only 1 response and response should be in json format) llm_response -  {"intent": "product_enquiry"}


Can you provide details about the availability status of the products and parts mentioned?(return only 1 response and response should be in json format) llm_response -  {"intent": "product_enquiry"}


What types of components are associated with the 1800W Table Saw (254mm) product in the Table Saws & Stands category?(return only 1 response and re

In [20]:
import huggingface_hub
huggingface_hub.login(token=access_token)
trainer.push_to_hub(new_model)

The token has not been saved to the git credentials helper. Pass `add_to_git_credential=True` in this function directly or `--add-to-git-credential` if using via `huggingface-cli` if you want to set the git credential as well.
Token is valid (permission: write).
Your token has been saved to /home/genai/.cache/huggingface/token
Login successful


adapter_model.safetensors:   0%|                                                                                           | 0.00/109M [00:00<?, ?B/s]
Upload 2 LFS files:   0%|                                                                                                       | 0/2 [00:00<?, ?it/s]

training_args.bin: 100%|█████████████████████████████████████████████████████████████████████████████████████████| 4.98k/4.98k [00:00<00:00, 5.60kB/s]
adapter_model.safetensors: 100%|███████████████████████████████████████████████████████████████████████████████████| 109M/109M [00:12<00:00, 8.46MB/s]

Upload 2 LFS files: 100%|███████████████████████████████████████████████████████████████████████████████████████████████| 2/2 [00:13<00:00,  6.83s/it]


CommitInfo(commit_url='https://huggingface.co/Akhil7766/dragon-mistral-7b-v0-Ryobi/commit/3036ac776d5b0e84e2d5253080bafa6a2550c270', commit_message='Akhil7766/dragon-mistral-7b-v0-Ryobi_29_May', commit_description='', oid='3036ac776d5b0e84e2d5253080bafa6a2550c270', pr_url=None, pr_revision=None, pr_num=None)